<!-- -*- mode: markdown; coding: utf-8; fill-column: 60; ispell-dictionary: "english";  eval: (visual-on);  -*- -->

<meta charset="utf-8"/>
<meta name="viewport" content="width=device-width,initial-scale=1"/>
<link rel="stylesheet" href="style.css">

# Normalization

In [ ]:
%load_ext sql

In [ ]:
%sql sqlite:///lect08.sqlite

## Make sure Sqlite checks foreign keys

In [ ]:
%%sql
PRAGMA foreign_keys=ON;

## Getting `movies` into BCNF

The original `movies` table, with some data:

In [ ]:
%%sql
DROP TABLE IF EXISTS movies;
CREATE TABLE movies (
  title       TEXT,
  year        INT,
  length      INT,
  category    TEXT,
  star        TEXT,
  PRIMARY KEY (title, year, star)
);

INSERT 
INTO    movies(title, year, length, category, star)
VALUES  ('The Post', 2017, 116, 'drama', 'Meryl Streep'),
        ('The Post', 2017, 116, 'drama', 'Tom Hanks'),
        ('The Post', 2017, 116, 'drama', 'Sarah Paulson'),
        ('The Post', 2017, 116, 'drama', 'Bob Odenkirk'),
        ('Three Billboards ...', 2017, 115, 'drama', 'Frances McDormand'),
        ('Three Billboards ...', 2017, 115, 'drama', 'Caleb Landry Jones'),
        ('Three Billboards ...', 2017, 115, 'drama', 'Kerry Condon'),
        ('Three Billboards ...', 2017, 115, 'drama', 'Sam Rockwell'),
        ('Lady Bird', 2017, 94, 'comedy', 'Saoirse Ronan'),
        ('Lady Bird', 2017, 94, 'comedy', 'Laurie Metcalf'),
        ('Lady Bird', 2017, 94, 'comedy', 'Tracy Letts'),
        ('Lady Bird', 2017, 94, 'comedy', 'Lucas Hedges');
        
SELECT  title, year, length, category, star
FROM    movies;

In [ ]:
%%sql
SELECT  title, year, length, category, star
FROM    movies;

A normalized (BCNF) version:

In [ ]:
%%sql
DROP TABLE IF EXISTS movie_data;
CREATE TABLE movie_data (
  title       TEXT,
  year        INT,
  length      INT,
  category    TEXT,
  PRIMARY KEY (title, year)
);

DROP TABLE IF EXISTS movie_stars;
CREATE TABLE movie_stars (
  title       TEXT,
  year        INT,
  star        TEXT,
  PRIMARY KEY (title, year, star)
);

In [ ]:
%%sql
INSERT
INTO   movie_data(title, year, length, category)
VALUES ('The Post', 2017, 116, 'drama'),
       ('Three Billboards ...', 2017 , 115, 'drama'),
       ('Lady Bird', 2017, 94, 'comedy');

INSERT
INTO   movie_stars(title, year, star)
VALUES ('The Post', 2017, 'Meryl Streep'),
       ('The Post', 2017, 'Tom Hanks'),
       ('The Post', 2017, 'Sarah Paulson'),
       ('The Post', 2017, 'Bob Odenkirk'),
       ('Three Billboards ...', 2017, 'Frances McDormand'),
       ('Three Billboards ...', 2017, 'Caleb Landry Jones'),
       ('Three Billboards ...', 2017, 'Kerry Condon'),
       ('Three Billboards ...', 2017, 'Sam Rockwell'),
       ('Lady Bird', 2017, 'Saoirse Ronan'),
       ('Lady Bird', 2017, 'Laurie Metcalf'),
       ('Lady Bird', 2017, 'Tracy Letts'),
       ('Lady Bird', 2017, 'Lucas Hedges');

In [ ]:
%%sql
SELECT *
FROM   movie_data;

In [ ]:
%%sql
SELECT *
FROM   movie_stars;

**Exercise:** How do we get our initial table `movies` back?

In [ ]:
%%sql
DROP TABLE IF EXISTS movies;
CREATE TABLE movies AS
  ...

SELECT *
FROM   movies
WHERE  title = 'The Post'
       AND year = 2017;

**Exercise:** How do we go in the other direction, i.e.,
create the two smaller tables from the redundant mess we
just created?

In [ ]:
%%sql
DROP TABLE IF EXISTS movie_stars;
CREATE TABLE movie_stars (
  title       TEXT,
  year        INT,
  star        TEXT,
  PRIMARY KEY (title, year, star),
  FOREIGN KEY (title, year) REFERENCES movie_data(title, year)
);

DROP TABLE IF EXISTS movie_data;
CREATE TABLE movie_data (
  title       TEXT,
  year        INT,
  length      INT,
  category    TEXT,
  PRIMARY KEY (title, year)
);

INSERT
INTO   movie_data(title, year, length, category)
...

INSERT
INTO   movie_stars(title, year, star)
...


In [ ]:
%%sql
SELECT *
FROM   movie_data;

In [ ]:
%%sql
SELECT *
FROM   movie_stars;

BTW, there is a simpler way of defining the tables above
(but then we can't define primary and foreign keys):

In [ ]:
%%sql
DROP TABLE IF EXISTS movie_stars;
CREATE TABLE movie_stars AS
SELECT DISTINCT title, year, star
FROM            movies;

DROP TABLE IF EXISTS movie_data;
CREATE TABLE movie_data AS
SELECT DISTINCT title, year, length, category
FROM            movies;

In [ ]:
%%sql
SELECT *
FROM   movie_data;

In [ ]:
%%sql
SELECT *
FROM   movie_stars;

Now back to the slides...

## Reconstruction

We first define our initial table `r(a,b,c)`:

In [ ]:
%%sql
DROP TABLE IF EXISTS r;
CREATE TABLE r (
  a   INT,
  b   INT,
  c   INT
);

INSERT
INTO   r(a,b,c)
VALUES (1,2,3),
       (2,2,4);

SELECT *
FROM   r;

We can decompose this into `r1(a,b)` and `r2(b,c)`:

In [ ]:
%%sql
DROP TABLE IF EXISTS r1;
DROP TABLE IF EXISTS r2;

CREATE TABLE r1 AS
SELECT a, b
FROM   r;

CREATE TABLE r2 AS
SELECT b, c
FROM   r;

In [ ]:
%%sql
SELECT *
FROM   r1;

In [ ]:
%%sql
SELECT *
FROM   r2;

**Exercise:** What do we get when we try to reconstruct the
original relation using the decomposition above?

In [ ]:
%%sql
SELECT a, b, c
FROM   r1
JOIN   r2
USING  (b);

**Exercise:** What do we get when we try to reconstruct the
original relation using our own BCNF-compliant
decomposition?

First we create a table `r3`:

In [ ]:
%%sql
DROP TABLE IF EXISTS r3;

CREATE TABLE r3 AS
SELECT a, c
FROM   r;

SELECT *
FROM   r3;


And then we join using `a`:

In [ ]:
%%sql
SELECT a, b, c
FROM   r1
JOIN   r3
USING  (a);

## Keeping Functional Dependencies

In [ ]:
%%sql
DROP TABLE IF EXISTS bookings;
CREATE TABLE bookings (
  title    TEXT,
  theater  TEXT,
  city     TEXT,
  unique   (theater),     -- because of FD1
  unique   (title, city)  -- because of FD2
);

In [ ]:
%%sql
INSERT
INTO   bookings(title, theater, city)
VALUES ('Phantom Thread', 'Guild', 'Menlo Park'),
       ('The Shape of Water', 'Park', 'Menlo Park');

FD2 prohibits the insertion of a title which is already
played in the city:

In [ ]:
%%sql
INSERT
INTO   bookings(title, theater, city)
VALUES ('Phantom Thread', 'Park', 'Menlo Park');

The table `bookings` is not in BCNF, but we can deconstruct
it into:

In [ ]:
%%sql
DROP TABLE IF EXISTS theaters;
CREATE TABLE theaters AS
  SELECT theater, city
  FROM   bookings;

DROP TABLE IF EXISTS performances;
CREATE TABLE performances AS
  SELECT theater, title
  FROM   bookings;

and everything looks fine when we reconstruct:

In [ ]:
%%sql
SELECT title, theater, city
FROM   theaters
JOIN   performances
USING  (theater);

However, we have no way to ensure FD2 holds -- it's now
possible to add a title which is already played in the city:

In [ ]:
%%sql
INSERT
INTO   performances(theater, title)
VALUES ('Park', 'Phantom Thread');

This would have been prohibited in `bookings`, because of a
`UNIQUE` constraint, now nothing is stopping us.

In [ ]:
%%sql
SELECT title, theater, city
FROM   theaters
JOIN   performances
USING  (theater);

If we want to keep FD2, we can keep `bookings`, which is in
3NF, since `city` is a member of a key. Redundance-wise
we're worse off than in BCNF, but we get to keep FD2 (and
will save some time when we want to know the city, since we
don't have to join `theaters` to get it).